# Quantum circuits and simulation of noisy algorithms

Welcome to this hands-on session. The session is build around interactive Notebooks, that include code, explanations and tasks. Please run the code cells on your computer and follow the instructions of the tasks to deepen your learning.    

Jami Rönkkö, IQM Quantum Computers, email: jami@meetiqm.com

# Basics of quantum circuits: measurement and two-qubit gates

In this notebook you will learn:
- how to emulate measurement of qubits
- entangle qubits with two-qubit gates

The statevector is a mathematical description of the quantum mechanical superposition state of the qubit(s). A fundamental axiom of quantum physics says that reading out or measuring a qubit will only yield classical outputs ∣0⟩ or ∣1⟩: **collapse of a wavefunction/statevector**.

The measurement outcome of a qubit in a superposition state is fundamentally non-deterministic. One can only assign probabilities for different outcomes. The probability of observing specific  computational state can be calculated by taking the square of the absolute value of the probability amplitude for that state. For example for the equal superposition state:
$$
\frac{\sqrt 2}{2}|0\hspace{-0.1cm}> - \frac{\sqrt 2}{2}|1\hspace{-0.1cm}> \hspace{1cm} (\textrm{this state is typically denoted as } |-\hspace{-0.1cm}>)
$$
The probabilites for the two measurement outcomes are obtained as:
$$
|\sqrt 2/2|^2=0.5 ~~\textrm{ and }~~ |-\sqrt 2/2|^2=0.5
$$
It is noteworthy that the phase of the state (here $e^{2\pi i}=-1$) does not affect the probability.


To emulate measurement of qubits in qiskit we have to:
- add to the circuit measurement operations and classical bits to store the output
- use simulator dedicated for measurement simulation     



In [ ]:
# Import everything from qiskit 
from qiskit import *

<font color='#5ACA97'><h2>TASK 1</h2></font>
> Read and run the three code snippets below to learn how to emulate measurement of a quantum circuit.
>
> Before running the last cell that executes the circuit, think what states you expect the measurements to register out of all possible *computational* two-qubit states: ∣00⟩, ∣01⟩, ∣10⟩ and ∣11⟩?

# Emulating measurement

In [ ]:
# Create a quantum circuit
circuit = QuantumCircuit(2,2)    # First argument is number of qubits and second is number of bits

# Add X gate to the first and H gate to the second qubit of the circuit
circuit.x(0)
circuit.h(1)                     

# Visualise the circuit
circuit.draw(output='mpl')

In [ ]:
circuit.measure([0,1],[0,1])           # Measure qubits 0 and 1 and store the result to classical bits 0 and 1, respectively

# Visualise the circuit
circuit.draw(output='mpl')

Before running the cell below, think what outcome(s) you expect by looking at the above circuit. Run the cell to see if you were right.

In [ ]:
simulator = Aer.get_backend("qasm_simulator")                          # Use qasm_simulator for circuit with measurements

result = execute(circuit, backend = simulator, shots = 11).result()    # Define how many circuit executions + measurements we do 

# Extract the result (measurement counts) from the executed job and look at the outcome
measurements = result.get_counts()

from qiskit.visualization import plot_histogram

plot_histogram(result.get_counts())


> Note: In Qiskit qubit indices in the statevector are read from right to left.

<font color='#5ACA97'><h2>TASK 2</h2></font>
> Increase the `shots` argument in the `execute` method in the cell above. Do the statistics of the measurement outcomes agree better with what you would expect based on the gates of the circuit? 
>
> Run statevector simulation below to verify the state of the qubits.

In [ ]:
from qiskit.visualization import plot_bloch_multivector

circuit.remove_final_measurements()                     # For statevector simulation we have to remove measurements from the circuit

result = execute(circuit, backend =  Aer.get_backend("statevector_simulator")).result()

result.get_statevector().draw("latex")

In [ ]:
plot_bloch_multivector(result.get_statevector())

From the state vector and Bloch spheres we see that first qubit is in state ∣1⟩ and second qubit is in the equal superposition of ∣0⟩ and ∣1⟩ with phase zero; typically called the ∣+⟩ state.

# Two-qubit gates and entanglement
We will now introduce the architypical entangling two-qubit gate: *CNOT* aka *controlled-NOT* aka *controlled-X*. 

<font color='#5ACA97'><h2>TASK 3</h2></font>
> Figure out the effect of `cx` (CNOT) gate by adding X gates to the beginning of the circuit below. Using the X gates, try the effect of `cx` to all possible computational two-qubit states: ∣00⟩, ∣01⟩, ∣01⟩ and ∣11⟩.
>
> What does the CNOT gate do?

In [ ]:
circuit = QuantumCircuit(2,2)

# Try adding X gates to: 1) neither 2) one 3) the other 4) both qubits

circuit.barrier() # Visual barrier that helps structuring circuits, it has no computational effect

# Apply CNOT gate using the first qubit as control and second as target
circuit.cx(0,1)

circuit.draw(output='mpl')

In [ ]:
# Solve and print the statevector
result = execute(circuit, backend = Aer.get_backend("statevector_simulator")).result()
result.get_statevector().draw("latex")


We can plot also the Bloch spheres of each qubit:

In [ ]:
plot_bloch_multivector(result.get_statevector())

We found out that CNOT applies X gate to the target qubit if control qubit is 1 and does nothing if target qubit is 0. It is equivalent to classical *reversible XOR gate*.

<font color='#5ACA97'><h2>TASK 4</h2></font>
> Go now back and add Hadamard gate to the control qubit. The bloch sphere plots seem to fail now, why is that?

**Answer:** 
The Bloch sphere visualization assumes that we can express the state of each qubit separately. By using the CNOT gate with the control qubit in a superposition state, we have *entangled* the qubits. The definition of entanglement is: **entangled qubits cannot be described with separate individual states**.

Two dimensional state i.e. state of a single qubit can be described by a Bloch sphere. Higher dimensional state vectors, that describe combined state of the qubits, would have to be visualised by higher dimensional hypersphere.

As a concrete example, consider two equal superposition states:
$$
\frac{\sqrt 2}{2}|01\hspace{-0.1cm}> + \frac{\sqrt 2}{2}|11\hspace{-0.1cm}> ~~\text{ and }~~ \frac{\sqrt 2}{2}|00\hspace{-0.1cm}> + \frac{\sqrt 2}{2}|11\hspace{-0.1cm}>
$$
The first two-qubit state can be described by saying that the first qubit is in state ∣1⟩ and second is in superposition of ∣0⟩ and ∣1⟩ i.e. the state is **separable**. Mathematically: 
$$
\frac{\sqrt 2}{2}|01\hspace{-0.1cm}> + \frac{\sqrt 2}{2}|11\hspace{-0.1cm}> = \left( \frac{\sqrt 2}{2}|0\hspace{-0.1cm}> + \frac{\sqrt 2}{2}|1\hspace{-0.1cm}>\right) \otimes |1\hspace{-0.1cm}>
$$

This is not possible for the second state. Instead we can say that first qubit is 1 iff the second qubit is 1 and 0 iff the second is 0. The qubits are entangled and need to be described by a shared statevector.

#### Disclaimer: Two-qubit gates don't always cause entanglement: it depends on the state we act upon
Above we saw that CNOT creates entanglement when control (or target) qubit is in superposition. Indeed without superposition CNOT is just a classical XOR gate. However, it might not be intuitive that 'too much' superposition will also cause CNOT to have no effect. To see this:
 1) run the cell below without cx gate 
 2) add cx gate and see if the final state changes

In [ ]:
circuit = QuantumCircuit(2)
circuit.h([0,1])
#circuit.cx(0, 1)

result = execute(circuit, backend = Aer.get_backend("statevector_simulator")).result()
result.get_statevector().draw("latex")

We see that the state is unaffected by the CNOT gate: in practice ∣01⟩ becomes ∣11⟩ and ∣11⟩ becomes ∣01⟩, so there is no actual change in the state.

The fact that equal superposition states (states that include equal amount of all computational basis) are separable, even if we apply two-qubit gates to them, will be useful in the next Notebook, where we will visualize such states with Bloch Spheres.

## Takeaway

- Real quantum computers cannot directly access the statevector of qubits \
 $\rightarrow$ only resulting probability distribution can be sampled by measurements 

 - Probability for finding qubit in some state ∣x⟩ in measurement is equal to the square of the absolute value of its probability amplitude: $P(x)=|a_x|^2$
 
- CNOT gate entagles qubits by making them be conditioned to each other's values

In the next notebook we consider compulsory step towards running circuits on real quantum computers: *transpilation*. 